In [1]:
# parse tree for propositional logic statements
#
class Propositional:
    
    # create a detached single node of a parse tree
    #
    def __init__(self, root_item):
        self._left = None
        self._right = None
        
        if root_item == "True":  # you might pass True but also the string "True"
            self._item = True
        elif root_item == "False":  # you might pass False but also the string "False"
            self._item = False
        else:
            self._item = root_item


    # returns a string representing the statement
    #
    def to_string(self):
        
        # note on syntax; there is a "match" control flow syntax
        # for this, but it only runs from Python 3.10 onward
        #
        if self._item is None:
            return "undefined"
        elif self._item == "not":
            return "not " + self._right.to_string()
        elif self._item == "or":
            return "(" + self._left.to_string() + " or " + self._right.to_string() + ")"
        elif self._item == "and":
            return "(" + self._left.to_string() + " and " + self._right.to_string() + ")"
        elif self._item == "->":
            return "(" + self._left.to_string() + " -> " + self._right.to_string() + ")"
        elif self._item == "<->":
            return "(" + self._left.to_string() + " <-> " + self._right.to_string() + ")"
        else:
            return self._item  # any other case: self._item is False, True, or an atomic statement
    

    # returns the number of nodes in the tree
    #
    def get_size(self):
        if self._item is None:  # not a valid node
            return 0
        size = 1
        if self._left is not None:
            size += self._left.get_size()
        if self._right is not None:
            size += self._right.get_size()
        return size

    
    # returns a set of atomic statement names occurring in the tree
    #
    def get_atomic_statements(self):
        if self._item is None:
            return set()  # empty set
        elif self._item in Propositional.non_leaf_items:
            atomic = self._right.get_atomic_statements()
            if self._left is not None:
                for el in self._left.get_atomic_statements():
                    atomic.add(el)
            return atomic
        elif self._item in {False, True}:
            return set()  # empty set
        else:
            return {self._item}  # in this case self is an atomic statement
    
    
    # removes all content from the tree
    #
    def clear(self):
        if self._left is not None:
            self._left.clear()
        if self._right is not None:
            self._right.clear()
        self._left = None
        self._item = None
        self._right = None

    
    # returns a new tree representing the statement "not self"
    #
    def negation(self):
        new_formula = Propositional("not")
        new_formula._right = self
        return new_formula
    
    # returns a new tree representing the statement "self or other"
    #
    def disjunction_with(self, other):
        new_formula = Propositional("or")
        new_formula._left = self
        new_formula._right = other
        return new_formula
    
    # returns a new tree representing the statement "self and other"
    #
    def conjunction_with(self, other):
        new_formula = Propositional("and")
        new_formula._left = self
        new_formula._right = other
        return new_formula
    
    # returns a new tree representing the statement "self -> other"
    #
    def conditional_with(self, other):
        new_formula = Propositional("->")
        new_formula._left = self
        new_formula._right = other
        return new_formula
    
    # returns a new tree representing the statement "self <-> other"
    #
    def biconditional_with(self, other):
        new_formula = Propositional("<->")
        new_formula._left = self
        new_formula._right = other
        print("\tWarning: <-> not implemented.", end="\t")
        return new_formula
    
    
    # returns the truth value for any given valuation
    #
    # the valuation is a dictionary, where keys are the atomic statements and values are False/True
    #
    def evaluate(self, valuation):

        left_evaluation = "undefined"
        if self._left is not None:
            left_evaluation = self._left.evaluate(valuation)
        right_evaluation = "undefined"
        if self._right is not None:
            right_evaluation = self._right.evaluate(valuation)
        
        # note on syntax; there is a "match" control flow syntax
        # for this, but it only runs from Python 3.10 onward
        #
        if self._item is None:
            return "undefined"
        elif self._item in {False, True}:
            return self._item
        elif self._item == "not":
            if right_evaluation == "undefined":
                return "undefined"
            return (not right_evaluation)
        elif self._item == "or":
            if left_evaluation == "undefined" or right_evaluation == "undefined":
                return "undefined"
            return (left_evaluation or right_evaluation)
        elif self._item == "and":
            if left_evaluation == "undefined" or right_evaluation == "undefined":
                return "undefined"
            return (left_evaluation and right_evaluation)
        elif self._item == "->":
            if left_evaluation == "undefined" or right_evaluation == "undefined":
                return "undefined"
            if not left_evaluation:
                return True
            else:
                return right_evaluation
        
        ######################
        # CODE MISSING BELOW #
        ######################
        #
        # implement this part as an exercise to get into this data structure
        #
        # we return "undefined" now, which should be True or False if
        # the left-hand side and the right-hand side can be evaluated
        #
        elif self._item == "<->":
            print("\tWarning: <-> not implemented.", end="\t")
            return "undefined"
        
        # any other case: self._item is an atomic statement;
        # in this case we can look up the truth value from the valuation
        #
        else:
            if self._item in valuation:
                return valuation[self._item]
            else:
                return "undefined"
    
    
    # generate and optionally print the truth table,
    # for a given set of atomic statements
    # (this may include atomics that don't occur in the formula)
    #
    # a potentially incomplete valuation is passed as the second argument;
    # these values are fixed and will not be varied
    #
    # output_flag controls whether a print(...) output is generated
    #
    # the complete truth table should be shown
    # for self.specific_truth_table(self.get_atomic_statements(), {}, True)
    #
    # the return value is a triple containing the number of True, False, and "undefined"
    # entries of the truth table, respectively
    #
    def specific_truth_table(self, atomic, valuation, output_flag):
        
        # loop over atomic until we find a variable without a given fixed truth value assignment
        #
        # then recursively distinguish the two possible cases, False and True
        #
        for variable in sorted(atomic):  # sorted is only used here to make the table look ordered
            if variable not in valuation:
                extended_valuation = valuation.copy()
                
                extended_valuation[variable] = False
                (true0, false0, und0) = \
                self.specific_truth_table(atomic, extended_valuation, output_flag)
                
                extended_valuation[variable] = True
                (true1, false1, und1) = \
                self.specific_truth_table(atomic, extended_valuation, output_flag)
                
                return (true0 + true1, false0 + false1, und0 + und1)  # add up True, False, undefined entries

        # if all the atomic statements were included in the valuation,
        # print out a single line of the truth table
        #
        boolean_value = self.evaluate(valuation)
        if output_flag:
            for variable in sorted(atomic):  # sorted is only used here to make the table look ordered
                if valuation[variable]:         # this blank space before "True" is just so that
                    print(" ", sep="", end="")  #  alignment in the table does not get messed up
                print(valuation[variable], "(", variable, ")", sep="", end="\t")
            print("<>\t", boolean_value)
        if boolean_value == "undefined":
            return (0, 0, 1)  # undefined
        elif boolean_value:
            return (1, 0, 0)  # True
        else:
            return (0, 1, 0)  # False
        
    def print_whole_truth_table(self):
        return self.specific_truth_table(self.get_atomic_statements(), {}, True)
    
    # returns the number of False entries in the truth table
    #
    def num_false_in_truth_table(self):
        (t, f, u) = self.specific_truth_table(self.get_atomic_statements(), {}, False)
        return f


    # items that signify that a node is not a leaf (similar but not identical to above)
    #
    non_leaf_items = {"and", "not", "or", "->", "<->"}

In [2]:
# let's look at a statement S, given by "(p -> not-q) and (q -> not-r) and (r -> not-s)" 

p_implies_not_q = Propositional("p").conditional_with(Propositional("q").negation())
q_implies_not_r = Propositional("q").conditional_with(Propositional("r").negation())
r_implies_not_s = Propositional("r").conditional_with(Propositional("s").negation())

statement_S = p_implies_not_q.conjunction_with(q_implies_not_r).conjunction_with(r_implies_not_s)

print("S:", statement_S.to_string())

S: (((p -> not q) and (q -> not r)) and (r -> not s))


In [3]:
print("Truth table of", p_implies_not_q.to_string(), "\n")
(t, f, u) = p_implies_not_q.print_whole_truth_table()
print("\nNumber of False entries:", p_implies_not_q.num_false_in_truth_table())

print("\nTruth table of S:", statement_S.to_string(), "\n")

(t, f, u) = statement_S.print_whole_truth_table()
print("\nNumber of False entries: ", f)

Truth table of (p -> not q) 

False(p)	False(q)	<>	 True
False(p)	 True(q)	<>	 True
 True(p)	False(q)	<>	 True
 True(p)	 True(q)	<>	 False

Number of False entries: 1

Truth table of S: (((p -> not q) and (q -> not r)) and (r -> not s)) 

False(p)	False(q)	False(r)	False(s)	<>	 True
False(p)	False(q)	False(r)	 True(s)	<>	 True
False(p)	False(q)	 True(r)	False(s)	<>	 True
False(p)	False(q)	 True(r)	 True(s)	<>	 False
False(p)	 True(q)	False(r)	False(s)	<>	 True
False(p)	 True(q)	False(r)	 True(s)	<>	 True
False(p)	 True(q)	 True(r)	False(s)	<>	 False
False(p)	 True(q)	 True(r)	 True(s)	<>	 False
 True(p)	False(q)	False(r)	False(s)	<>	 True
 True(p)	False(q)	False(r)	 True(s)	<>	 True
 True(p)	False(q)	 True(r)	False(s)	<>	 True
 True(p)	False(q)	 True(r)	 True(s)	<>	 False
 True(p)	 True(q)	False(r)	False(s)	<>	 False
 True(p)	 True(q)	False(r)	 True(s)	<>	 False
 True(p)	 True(q)	 True(r)	False(s)	<>	 False
 True(p)	 True(q)	 True(r)	 True(s)	<>	 False

Number of False entries:  8


In [4]:
# now the same for the statement R, given by (p and q) <-> (q and r)
#
p_and_q = Propositional("p").conjunction_with(Propositional("q"))
q_and_r = Propositional("q").conjunction_with(Propositional("r"))
print("Truth table of", p_and_q.to_string(), "\n")
(t, f, u) = p_and_q.print_whole_truth_table()
print("\nNumber of False entries: ", f)

statement_R = p_and_q.biconditional_with(q_and_r)

print("\n\nTruth table of R:", statement_R.to_string(), "\n")

(t, f, u) = statement_R.print_whole_truth_table()
print("\nNumber of False entries:", statement_R.num_false_in_truth_table())

Truth table of (p and q) 

False(p)	False(q)	<>	 False
False(p)	 True(q)	<>	 False
 True(p)	False(q)	<>	 False
 True(p)	 True(q)	<>	 True

Number of False entries:  3

Truth table of R: ((p and q) <-> (q and r)) 

Number of False entries: 0


In [5]:
# as another example, let us create a "False" statement
# (which should not contain any atomic statements like p, q, ...)
#
# and still output a table with p, q, and r
#
false_statement = Propositional(False)
print("\nTruth table of", false_statement.to_string(), "with some additional variables\n")
(t, f, u) = false_statement.specific_truth_table({"p", "q", "r"}, {}, True)
print("\nNumber of False entries: ", f)


Truth table of False with some additional variables

False(p)	False(q)	False(r)	<>	 False
False(p)	False(q)	 True(r)	<>	 False
False(p)	 True(q)	False(r)	<>	 False
False(p)	 True(q)	 True(r)	<>	 False
 True(p)	False(q)	False(r)	<>	 False
 True(p)	False(q)	 True(r)	<>	 False
 True(p)	 True(q)	False(r)	<>	 False
 True(p)	 True(q)	 True(r)	<>	 False

Number of False entries:  8


In [6]:
not_p = Propositional("p").negation()
p_and_not_p = Propositional("p").conjunction_with(not_p)

print(p_and_not_p.to_string(), end="\n\n")
(t, f, u) = p_and_not_p.print_whole_truth_table()
print("\nNumber of False entries:", p_and_not_p.num_false_in_truth_table())

(p and not p)

False(p)	<>	 False
 True(p)	<>	 False

Number of False entries: 2


In [7]:
# below, a helper function that might be useful for implementing
# an algorithm that creates a Propositional object with n entries
# in the truth table that are False

# you are not required to use this - ignore it if you don't think it would help

# argument: a natural number n
# return value: a list representing that same number by a sequence of binary digits
#
def natural_number_to_binary_list(n):
    if n == 0:
        return []
    digits, final_digit = natural_number_to_binary_list(n//2), n%2
    digits.append(final_digit)
    return digits

In [8]:
print(natural_number_to_binary_list(47))  # the binary number version of 47 is 101111

[1, 0, 1, 1, 1, 1]
